In [1]:
%load_ext autoreload
%autoreload 2

In [81]:
import pandas as pd
from sklearn.metrics.pairwise import cosine_similarity
import scoring
import helpers

In [3]:
resumes = pd.read_parquet('processed/resume_embeddings.parquet')

In [4]:
jobs = pd.read_parquet('processed/dice_job_descriptions_embeddings.parquet')

In [5]:
resumes

ID                                         Resume_str  \
0     16852973           HR ADMINISTRATOR/MARKETING ASSOCIATE\...   
1     22323967           HR SPECIALIST, US HR OPERATIONS      ...   
2     33176873           HR DIRECTOR       Summary      Over 2...   
3     27018550           HR SPECIALIST       Summary    Dedica...   
4     17812897           HR MANAGER         Skill Highlights  ...   
...        ...                                                ...   
2479  99416532           RANK: SGT/E-5 NON- COMMISSIONED OFFIC...   
2480  24589765           GOVERNMENT RELATIONS, COMMUNICATIONS ...   
2481  31605080           GEEK SQUAD AGENT         Professional...   
2482  21190805           PROGRAM DIRECTOR / OFFICE MANAGER    ...   
2483  37473139           STOREKEEPER II       Professional Sum...   

                                            Resume_html  Category  \
0     <div class="fontsize fontface vmargins hmargin...        HR   
1     <div class="fontsize fontface vmargins hmargin...        HR   
2     <div class="fontsize fontface vmargins hmargin...        HR   
3     <div class="fontsize fontface vmargins hmargin...        HR   
4     <div class="fontsize fontface vmargins hmargin...        HR   
...                                                 ...       ...   
2479  <div class="fontsize fontface vmargins hmargin...  AVIATION   
2480  <div class="fontsize fontface vmargins hmargin...  AVIATION   
2481  <div class="fontsize fontface vmargins hmargin...  AVIATION   
2482  <div class="fontsize fontface vmargins hmargin...  AVIATION   
2483  <div class="fontsize fontface vmargins hmargin...  AVIATION   

                                       extracted_skills  length  \
0     [Accounting, Ads, Advertising, Analytical skil...    5442   
1     [Adobe Photoshop, ADP, Asset Management, brand...    5572   
2     [Recruiting, FMLA/EEO/FLSA, HRIS Development, ...    7720   
3     [Type 50 wpm and 10-Key by touch, Microsoft pr...    2855   
4     [ADA, ADP, art, agency, benefits, Benefits Adm...    9172   
...                                                 ...     ...   
2479  [Secret Clearance, Stock Control, Management, ...    5533   
2480  [arbitration, agency, budgets, Budget, continu...    7108   
2481  [Active Directory, Hardware, Customer Service,...    2020   
2482  [Adobe, CPR, Customer Service, Customer Care, ...    5074   
2483  [Architectural Drafting, AutoCAD, Customer Ser...    5234   

                                         matched_skills  \
0     [accounting, create advertisements, outdoor ad...   
1     [Adobe Photoshop, asset management, maintain c...   
2     [recruit members, foreign affairs policy devel...   
3     [personnel management, customer service, resol...   
4     [create artwork, coaching techniques, coaching...   
...                                                 ...   
2479  [follow stock control instructions, operations...   
2480  [examine budgets, update budget, continuous im...   
2481  [hardware materials, customer service, manage ...   
2482  [customer service, maintain customer service, ...   
2483  [create architectural sketches, customer servi...   

                                 matched_skills_ordered  \
0     [accounting, company policies, conduct public ...   
1     [Adobe Illustrator, Adobe Photoshop, asset man...   
2     [Microsoft Access, desktop publishing, foreign...   
3     [customer service, personnel management, resol...   
4     [Microsoft Access, Microsoft Visio, coaching t...   
...                                                 ...   
2479  [communication, follow stock control instructi...   
2480  [Microsoft Visio, computer graphics, continuou...   
2481  [assemble windows, customer service, hardware ...   
2482  [Microsoft Access, chair a meeting, customer s...   
2483  [advise on safety measures, advise supervisors...   

                                       skill_embeddings  \
0     [-0.051119804, 0.051380936, -0.1956489, -0.000...   
1     [-0.013

In [6]:
jobs

advertiserurl  \
0      https://www.dice.com/jobs/detail/AUTOMATION-TE...   
1      https://www.dice.com/jobs/detail/Information-S...   
2      https://www.dice.com/jobs/detail/Business-Solu...   
3      https://www.dice.com/jobs/detail/Java-Develope...   
4      https://www.dice.com/jobs/detail/DevOps-Engine...   
...                                                  ...   
21995  https://www.dice.com/jobs/detail/Web-Designer-...   
21996  https://www.dice.com/jobs/detail/Senior-Front-...   
21997  https://www.dice.com/jobs/detail/QA-Analyst-Sa...   
21998  https://www.dice.com/jobs/detail/Tech-Lead%252...   
21999  https://www.dice.com/jobs/detail/C%2526%252347...   

                                 company  \
0      Digital Intelligence Systems, LLC   
1      University of Chicago/IT Services   
2                   Galaxy Systems, Inc.   
3                          TransTech LLC   
4                       Matrix Resources   
...                                  ...   
21995                     IAC Publishing   
21996                Omega Solutions Inc   
21997          San Francisco Health Plan   
21998                     IAC Publishing   
21999          Technology Resource Group   

                                employmenttype_jobstatus  \
0      C2H Corp-To-Corp, C2H Independent, C2H W2, 3 M...   
1                                              Full Time   
2                                              Full Time   
3                                              Full Time   
4                                              Full Time   
...                                                  ...   
21995                                          Full Time   
21996                                          Full Time   
21997                                          Full Time   
21998                                          Full Time   
21999                               Full Time, Full Time   

                                          jobdescription               jobid  \
0      Looking for Selenium engineers...must have sol...  Dice Id : 10110693   
1      The University of Chicago has a rapidly growin...  Dice Id : 10114469   
2      GalaxE.SolutionsEvery day, our solutions affec...  Dice Id : CXGALXYS   
3      Java DeveloperFull-time/direct-hireBolingbrook...  Dice Id : 10113627   
4      Midtown based high tech firm has an immediate ...  Dice Id : matrixga   
...                                                  ...                 ...   
21995   Company Description We are searching for a ta...  Dice Id : 10112803   
21996   CONTACT - priya@omegasolutioninc.com / 408-45...  Dice Id : 10289500   
21997  Do you take pride in your work knowing that th...  Dice Id : 10115761   
21998  Company Description What We Can Offer YouAs th...  Dice Id : 10112803   
21999  Experience in C/C++ ProgrammingDevelopment exp...  Dice Id : 90734436   

      joblocation_address                                           jobtitle  \
0             Atlanta, GA                           AUTOMATION TEST ENGINEER   
1             Chicago, IL                      Information Security Engineer   
2          Schaumburg, IL                       Business Solutions Architect   
3         Bolingbrook, IL  Java Developer (mid level)- FT- GREAT culture,...   
4             Atlanta, GA                                    DevOps Engineer   
...                   ...                                                ...   
21995         Oakland, CA                                       Web Designer   
21996   San Francisco, CA  Senior Front End Web Developer - Full Time at ...   
21997   San Francisco, CA                                         QA Analyst   
21998         Oakland, CA                               Tech Lead-Full Stack   
21999     Santa Clara, CA                                   C/C++ Programmer   

             postdate                                            shift  \
0          1 hour ago  Telecommuting not available|Travel not required   
1 

In [7]:
resumes['Category'].value_counts()

Category
INFORMATION-TECHNOLOGY    120
BUSINESS-DEVELOPMENT      120
ADVOCATE                  118
CHEF                      118
ENGINEERING               118
ACCOUNTANT                118
FINANCE                   118
FITNESS                   117
AVIATION                  117
SALES                     116
BANKING                   115
HEALTHCARE                115
CONSULTANT                115
CONSTRUCTION              112
PUBLIC-RELATIONS          111
HR                        110
DESIGNER                  107
ARTS                      103
TEACHER                   102
APPAREL                    97
DIGITAL-MEDIA              96
AGRICULTURE                63
AUTOMOBILE                 36
BPO                        22
Name: count, dtype: int64

In [8]:
resumes[resumes['Category']=='INFORMATION-TECHNOLOGY']

ID                                         Resume_str  \
217  36856210           INFORMATION TECHNOLOGY         Summar...   
218  21780877           INFORMATION TECHNOLOGY SPECIALIST\tGS...   
219  33241454           INFORMATION TECHNOLOGY SUPERVISOR    ...   
220  25990239           INFORMATION TECHNOLOGY INSTRUCTOR    ...   
221  16899268           INFORMATION TECHNOLOGY MANAGER/ANALYS...   
..        ...                                                ...   
332  27485716           CORPORATE PROJECT MANAGER       Caree...   
333  26480367           IT TECHNOLOGY SPECIALIST       Profes...   
334  81761658           IT MANAGER             Highlights    ...   
335  79541391           SUBJECT MATTER EXPERT (INFORMATION TE...   
336  23666211           TRAINING MANAGER         Executive Su...   

                                           Resume_html  \
217  <div class="fontsize fontface vmargins hmargin...   
218  <div class="fontsize fontface vmargins hmargin...   
219  <div class="fontsize fontface vmargins hmargin...   
220  <div class="fontsize fontface vmargins hmargin...   
221  <div class="fontsize fontface vmargins hmargin...   
..                                                 ...   
332  <div class="fontsize fontface vmargins hmargin...   
333  <div class="fontsize fontface vmargins hmargin...   
334  <div class="fontsize fontface vmargins hmargin...   
335  <div class="fontsize fontface vmargins hmargin...   
336  <div class="fontsize fontface vmargins hmargin...   

                   Category  \
217  INFORMATION-TECHNOLOGY   
218  INFORMATION-TECHNOLOGY   
219  INFORMATION-TECHNOLOGY   
220  INFORMATION-TECHNOLOGY   
221  INFORMATION-TECHNOLOGY   
..                      ...   
332  INFORMATION-TECHNOLOGY   
333  INFORMATION-TECHNOLOGY   
334  INFORMATION-TECHNOLOGY   
335  INFORMATION-TECHNOLOGY   
336  INFORMATION-TECHNOLOGY   

                                      extracted_skills  length  \
217  [Enterprise platforms, Product Lifecycle Manag...    4888   
218  [budget, cabling, cisco, hardware, Client, doc...    6491   
219  [Army, Cisco, counseling, customer assistance,...    4447   
220  [Data Analysis, Curriculum design, Advanced Da...    6443   
221  [Project management, Program management, Proce...    4203   
..                                                 ...     ...   
332  [Strategic Planning, Visioning & Tactical Exec...    6358   
333  [TCP/IP, Network monitoring and tools, storage...    5296   
334  [Antivirus, Backup Exec, Backup, budget, Cisco...    6956   
335  [SAP, HP ALM, Network Configuration, Database ...   13149   
336  [Training and Development, Supervision and tra...    6237   

                                        matched_skills  \
217  [Microsoft Visio, establish collaborative rela...   
218  [update budget, Cisco, hardware materials, cou...   
219  [Cisco, assist customers, database, documentat...   
220  [perform data analysis, advise on curriculum d...   
221  [project management, program management, ident...   
..                                                 ...   
332  [strategic planning, apply change management, ...   
333  [network management system tools, manage stora...   
334  [perform backups, update budget, Cisco, Cisco,...   
335  [analyse network configuration and performance...   
336  [develop training programmes, advise on curric...   

                                matched_skills_ordered  \
217  [Microsoft Visio, analyse network configuratio...   
218  [Cisco, Microsoft Access, build networks, comp...   
219  [Cisco, assist customers, call routing, compan...   
220  [Adobe Illustrator, Adobe Photoshop, PHP, advi...   
221  [identify process improvements, lead a team, p...   
..                                                 ...   
332  [apply change management, coordinate security,...   
333  [manage storage operations, network management...   
334  [Cisco, company policies, computer technology,...   
335  [ASP.NET, Microsoft Access, SQL, analyse netwo...

In [9]:
job_embeddings = jobs['skill_embeddings_ordered'].tolist()

In [10]:
resume = resumes.iloc[0]

In [11]:
embedding = resume['skill_embeddings_ordered']

In [12]:
print(resume['matched_skills'])

['accounting' 'create advertisements' 'outdoor advertising'
 'monitor billing procedures' 'manage budgets' 'customer service'
 'perform data analysis' 'documentation types' 'financial management'
 'maintain relationships with government agencies' 'hire human resources'
 'types of insurance' 'store design layout' 'services marketing'
 'medical terminology' 'office administration' 'manage payroll'
 'recruit personnel' 'company policies' 'hang advertising posters'
 'conduct public presentations' 'public relations' 'statistics'
 'manage website']


In [13]:
distances = cosine_similarity([embedding], job_embeddings)

In [14]:
distances.max()

np.float64(0.7809325420344598)

In [15]:
distances.argmax()

np.int64(17293)

In [16]:
def get_metrics(list1, list2):
    set1 = set(list1)
    set2 = set(list2)

    overlap = set1 & set2
    difference = set1 ^ set2

    print(f"Overlap: {len(overlap)}")
    print(f"No Overlap: {len(difference)} ")

In [17]:
resume['matched_skills']

array(['accounting', 'create advertisements', 'outdoor advertising',
       'monitor billing procedures', 'manage budgets', 'customer service',
       'perform data analysis', 'documentation types',
       'financial management',
       'maintain relationships with government agencies',
       'hire human resources', 'types of insurance',
       'store design layout', 'services marketing', 'medical terminology',
       'office administration', 'manage payroll', 'recruit personnel',
       'company policies', 'hang advertising posters',
       'conduct public presentations', 'public relations', 'statistics',
       'manage website'], dtype=object)

In [18]:
jobs['matched_skills'].iloc[distances.argmax()]

array(['align efforts towards business development', 'communication',
       'provide technical expertise', 'sales strategies',
       'offer financial services', 'entertain people',
       'types of insurance'], dtype=object)

In [19]:
get_metrics(resume['matched_skills'], jobs['matched_skills'].iloc[distances.argmax()])

Overlap: 1
No Overlap: 29 


In [20]:
resume_embeddings = resumes['skill_embeddings_ordered'].tolist()

In [21]:
job_embeddings = jobs['skill_embeddings_ordered'].tolist()

In [22]:
similarities = cosine_similarity(resume_embeddings, job_embeddings)

In [23]:
best_match_indices = similarities.argmax(axis=1)
best_match_scores = similarities.max(axis=1)

In [24]:
resumes['best_match_index'] = best_match_indices
resumes['best_match_score'] = best_match_scores
resumes['best_match_job_embedding'] = jobs.loc[best_match_indices, 'skill_embeddings_ordered'].values
resumes['best_match_job_skills'] = jobs.loc[best_match_indices, 'matched_skills_ordered'].values

In [80]:
resumes

ID                                         Resume_str  \
0     16852973           HR ADMINISTRATOR/MARKETING ASSOCIATE\...   
1     22323967           HR SPECIALIST, US HR OPERATIONS      ...   
2     33176873           HR DIRECTOR       Summary      Over 2...   
3     27018550           HR SPECIALIST       Summary    Dedica...   
4     17812897           HR MANAGER         Skill Highlights  ...   
...        ...                                                ...   
2479  99416532           RANK: SGT/E-5 NON- COMMISSIONED OFFIC...   
2480  24589765           GOVERNMENT RELATIONS, COMMUNICATIONS ...   
2481  31605080           GEEK SQUAD AGENT         Professional...   
2482  21190805           PROGRAM DIRECTOR / OFFICE MANAGER    ...   
2483  37473139           STOREKEEPER II       Professional Sum...   

                                            Resume_html  Category  \
0     <div class="fontsize fontface vmargins hmargin...        HR   
1     <div class="fontsize fontface vmargins hmargin...        HR   
2     <div class="fontsize fontface vmargins hmargin...        HR   
3     <div class="fontsize fontface vmargins hmargin...        HR   
4     <div class="fontsize fontface vmargins hmargin...        HR   
...                                                 ...       ...   
2479  <div class="fontsize fontface vmargins hmargin...  AVIATION   
2480  <div class="fontsize fontface vmargins hmargin...  AVIATION   
2481  <div class="fontsize fontface vmargins hmargin...  AVIATION   
2482  <div class="fontsize fontface vmargins hmargin...  AVIATION   
2483  <div class="fontsize fontface vmargins hmargin...  AVIATION   

                                       extracted_skills  length  \
0     [Accounting, Ads, Advertising, Analytical skil...    5442   
1     [Adobe Photoshop, ADP, Asset Management, brand...    5572   
2     [Recruiting, FMLA/EEO/FLSA, HRIS Development, ...    7720   
3     [Type 50 wpm and 10-Key by touch, Microsoft pr...    2855   
4     [ADA, ADP, art, agency, benefits, Benefits Adm...    9172   
...                                                 ...     ...   
2479  [Secret Clearance, Stock Control, Management, ...    5533   
2480  [arbitration, agency, budgets, Budget, continu...    7108   
2481  [Active Directory, Hardware, Customer Service,...    2020   
2482  [Adobe, CPR, Customer Service, Customer Care, ...    5074   
2483  [Architectural Drafting, AutoCAD, Customer Ser...    5234   

                                         matched_skills  \
0     [accounting, create advertisements, outdoor ad...   
1     [Adobe Photoshop, asset management, maintain c...   
2     [recruit members, foreign affairs policy devel...   
3     [personnel management, customer service, resol...   
4     [create artwork, coaching techniques, coaching...   
...                                                 ...   
2479  [follow stock control instructions, operations...   
2480  [examine budgets, update budget, continuous im...   
2481  [hardware materials, customer service, manage ...   
2482  [customer service, maintain customer service, ...   
2483  [create architectural sketches, customer servi...   

                                 matched_skills_ordered  \
0     [accounting, company policies, conduct public ...   
1     [Adobe Illustrator, Adobe Photoshop, asset man...   
2     [Microsoft Access, desktop publishing, foreign...   
3     [customer service, personnel management, resol...   
4     [Microsoft Access, Microsoft Visio, coaching t...   
...                                                 ...   
2479  [communication, follow stock control instructi...   
2480  [Microsoft Visio, computer graphics, continuou...   
2481  [assemble windows, customer service, hardware ...   
2482  [Microsoft Access, chair a meeting, customer s...   
2483  [advise on safety measures, advise supervisors...   

                                       skill_embeddings  \
0     [-0.051119804, 0.051380936, -0.1956489, -0.000...   
1     [-0.013

In [79]:
resumes['true_missing'] = resumes.apply(
    lambda row: list(set(row['best_match_job_skills']) - set(row['matched_skills_ordered'])),
    axis=1
)

In [84]:
resumes['predicted_missing'] = resumes.apply(
    lambda row: helpers.predict_missing(row, job_embeddings, jobs),
    axis=1
)

In [85]:
resumes['best_match_score'].mean()

np.float64(0.8327406902376754)

In [142]:
index = 15
print("Job Description")
print(resumes['best_match_job_skills'].iloc[index])
print()
print("Sample Resume")
print(resumes['matched_skills_ordered'].iloc[index])

Job Description
['adjust priorities' 'customer service' 'discern written communication'
 'make decisions' 'meet deadlines' 'office software'
 'perform data analysis' 'perform multiple tasks at the same time'
 'project management' 'quality standards' 'solve problems'
 'transportation software related to an ERP system' 'troubleshoot']

Sample Resume
['customer service' 'follow up accounts receivables' 'listen actively'
 'manage standard enterprise resource planning system']


In [143]:
true_missing = set(resumes['best_match_job_skills'].iloc[index])-set(resumes['matched_skills_ordered'].iloc[index])

In [155]:
predicted_missing-true_missing

{'customer service'}

In [156]:
true_missing-predicted_missing

set()

In [145]:
set(resumes['true_missing'].iloc[index])

{'adjust priorities',
 'discern written communication',
 'make decisions',
 'meet deadlines',
 'office software',
 'perform data analysis',
 'perform multiple tasks at the same time',
 'project management',
 'quality standards',
 'solve problems',
 'transportation software related to an ERP system',
 'troubleshoot'}

In [146]:
len(true_missing)

12

In [147]:
diff = resumes['best_match_job_embedding'].iloc[index] - resumes['skill_embeddings_ordered'].iloc[index]

In [148]:
diffs = cosine_similarity([diff], job_embeddings)

In [149]:
diffs.argmax()

np.int64(18923)

In [150]:
predicted_missing = set(jobs['matched_skills_ordered'].iloc[diffs.argmax()])

In [151]:
predicted_missing

{'adjust priorities',
 'customer service',
 'discern written communication',
 'make decisions',
 'meet deadlines',
 'office software',
 'perform data analysis',
 'perform multiple tasks at the same time',
 'project management',
 'quality standards',
 'solve problems',
 'transportation software related to an ERP system',
 'troubleshoot'}

In [152]:
true_missing.intersection(predicted_missing)

{'adjust priorities',
 'discern written communication',
 'make decisions',
 'meet deadlines',
 'office software',
 'perform data analysis',
 'perform multiple tasks at the same time',
 'project management',
 'quality standards',
 'solve problems',
 'transportation software related to an ERP system',
 'troubleshoot'}

In [153]:
predicted_missing-true_missing

{'customer service'}

In [128]:
print(len(true_missing.intersection(predicted_missing)))
print(len(true_missing-predicted_missing))

2
10


In [109]:
true_missing.symmetric_difference(predicted_missing)

{'customer relationship management',
 'leadership principles',
 'manage a team',
 'perform data analysis',
 'perform political negotiation',
 'plan ',
 'printing techniques',
 'repair mobile devices',
 'show initiative',
 'solve problems',
 'supplier management',
 'think creatively'}

In [92]:
resumes['true_missing'].tolist()

[['communication',
  'sales strategies',
  'provide technical expertise',
  'offer financial services',
  'align efforts towards business development',
  'entertain people'],
 ['digital media',
  'perform data analysis',
  'adobe creative suite',
  'execute email marketing',
  'iconography',
  'supplier management'],
 ['Microsoft Visio',
  'solve problems',
  'communication',
  'perform multiple tasks at the same time',
  'project management',
  'document management',
  'personal development',
  'risk identification',
  'prepare presentation material',
  'perform political negotiation',
  'program management'],
 ['solve problems',
  'communication',
  'organise training',
  'conflict management',
  'negotiate sales contracts',
  'manage major incidents'],
 ['solve problems',
  'communication',
  'organise training',
  'perform multiple tasks at the same time',
  'document management',
  'personal development',
  'risk identification',
  'prepare presentation material',
  'perform polit

In [95]:
scoring.found(resumes['true_missing'].tolist(),resumes['predicted_missing'].tolist())

np.float64(0.6294788131442721)

In [158]:
scoring.unnecessary_score(resumes['true_missing'].tolist(),resumes['predicted_missing'].tolist())

np.float64(0.298341644294956)

In [160]:
scoring.redundant_score(resumes['predicted_missing'].tolist(), resumes['matched_skills_ordered'].tolist())

np.float64(0.15023986796250335)

v(queen) ~= ....

v(missing skills) ~= ...